In [1]:
import pandas as pd
import numpy as np
import seaborn as sb
from matplotlib import pyplot as plt
from datetime import datetime
import string

from transformers import AutoTokenizer, AutoModelForSequenceClassification
from nltk.tokenize import TweetTokenizer
from scipy.special import softmax

import nltk

import re


import torch
import os

In [2]:
data = pd.read_csv('preprocessed_data.csv')

In [3]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 287188 entries, 0 to 287187
Data columns (total 20 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   id                   287187 non-null  float64
 1   createdAt            287188 non-null  object 
 2   fullName             287149 non-null  object 
 3   userName             287188 non-null  object 
 4   profileImage         287188 non-null  object 
 5   fullText             287188 non-null  object 
 6   replyTo              287188 non-null  int64  
 7   lang                 287188 non-null  object 
 8   quoteCount           287188 non-null  int64  
 9   retweetCount         287188 non-null  int64  
 10  replyCount           287188 non-null  int64  
 11  likeCount            287188 non-null  int64  
 12  viewCount            103504 non-null  float64
 13  sentimentLabel1      1790 non-null    float64
 14  sentimentLabel2      1201 non-null    float64
 15  sentimentLabel3  

# RoBerta

In [4]:
labeled_data = data[data['sentimentLabelFinal'].notnull()]

In [9]:
labeled_data = labeled_data[labeled_data['cleaned_tweet_vader'].notnull()]

In [5]:
labeled_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 996 entries, 152428 to 153426
Data columns (total 20 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   id                   996 non-null    float64
 1   createdAt            996 non-null    object 
 2   fullName             996 non-null    object 
 3   userName             996 non-null    object 
 4   profileImage         996 non-null    object 
 5   fullText             996 non-null    object 
 6   replyTo              996 non-null    int64  
 7   lang                 996 non-null    object 
 8   quoteCount           996 non-null    int64  
 9   retweetCount         996 non-null    int64  
 10  replyCount           996 non-null    int64  
 11  likeCount            996 non-null    int64  
 12  viewCount            0 non-null      float64
 13  sentimentLabel1      996 non-null    float64
 14  sentimentLabel2      996 non-null    float64
 15  sentimentLabel3      996 non-null    

In [6]:
labeled_data['sentimentLabelFinal'].value_counts()

sentimentLabelFinal
1.0    497
0.0    355
2.0    144
Name: count, dtype: int64

In [7]:
from transformers import AutoModelForSequenceClassification, AutoTokenizer, AutoConfig, AdamW

In [ ]:
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from sklearn.model_selection import train_test_split
from torch.utils.data import DataLoader, TensorDataset, RandomSampler, SequentialSampler
from tqdm import tqdm
from sklearn.metrics import classification_report


# Load your datasets
# Assuming your datasets are 'data' and 'labeled_data' DataFrames

# Split labeled data into train and validation sets
train_data, val_data = train_test_split(labeled_data, test_size=0.2, random_state=42)

# Load pre-trained RoBERTa tokenizer
MODEL = "cardiffnlp/twitter-roberta-base-sentiment-latest"
tokenizer = AutoTokenizer.from_pretrained(MODEL)
config = AutoConfig.from_pretrained(MODEL)

# Tokenize text data
train_encodings = tokenizer(list(train_data['cleaned_tweet']), truncation=True, padding=True, max_length=128, return_tensors='pt')
val_encodings = tokenizer(list(val_data['cleaned_tweet']), truncation=True, padding=True, max_length=128, return_tensors='pt')

# Convert labels to tensors of type torch.long
train_labels = torch.tensor(list(train_data['sentimentLabelFinal']), dtype=torch.long)
val_labels = torch.tensor(list(val_data['sentimentLabelFinal']), dtype=torch.long)

# Define TensorDatasets for training and validation
train_dataset = TensorDataset(train_encodings['input_ids'], train_encodings['attention_mask'], train_labels)
val_dataset = TensorDataset(val_encodings['input_ids'], val_encodings['attention_mask'], val_labels)

# Initialize the model
model = AutoModelForSequenceClassification.from_pretrained(MODEL, config=config)

# Define training parameters
batch_size = 32
epochs = 3
learning_rate = 2e-5

# Define optimizer and loss function
optimizer = AdamW(model.parameters(), lr=learning_rate)
loss_fn = nn.CrossEntropyLoss()

# Prepare DataLoader for training and validation
train_loader = DataLoader(train_dataset, batch_size=batch_size, sampler=RandomSampler(train_dataset))
val_loader = DataLoader(val_dataset, batch_size=batch_size, sampler=SequentialSampler(val_dataset))


In [ ]:
# Training loop
model.train()
for epoch in range(epochs):
    total_loss = 0
    for batch in tqdm(train_loader, desc=f'Epoch {epoch + 1}', unit='batches'):
        input_ids, attention_mask, labels = batch
        optimizer.zero_grad()
        logits = model(input_ids, attention_mask=attention_mask).logits
        loss = loss_fn(logits, labels)
        total_loss += loss.item()
        loss.backward()
        optimizer.step()
    print(f'Epoch {epoch + 1}, Loss: {total_loss / len(train_loader)}')

# Evaluation
model.eval()
all_preds, all_labels = [], []
with torch.no_grad():
    for batch in tqdm(val_loader, desc='Evaluation', unit='batches'):
        input_ids, attention_mask, labels = batch
        logits = model(input_ids, attention_mask=attention_mask).logits
        preds = torch.argmax(logits, dim=1)
        all_preds.extend(preds.cpu().numpy())
        all_labels.extend(labels.cpu().numpy())

# Calculate classification report
report = classification_report(all_labels, all_preds, target_names=['Positive', 'Negative', 'Neutral'])
print("Classification Report:")
print(report)


Some weights of the model checkpoint at cardiffnlp/twitter-roberta-base-sentiment-latest were not used when initializing RobertaForSequenceClassification: ['roberta.pooler.dense.bias', 'roberta.pooler.dense.weight']
- This IS expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:429: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this w

Epoch 1, Loss: 0.7823317933082581


Epoch 2: 100%|██████████| 25/25 [04:20<00:00, 10.43s/batches]


Epoch 2, Loss: 0.5817028594017029


Epoch 3: 100%|██████████| 25/25 [04:22<00:00, 10.52s/batches]


Epoch 3, Loss: 0.4092314159870148


Evaluation: 100%|██████████| 7/7 [00:20<00:00,  2.94s/batches]

Classification Report:
              precision    recall  f1-score   support

    Positive       0.67      0.49      0.57        63
    Negative       0.68      0.79      0.73       102
     Neutral       0.73      0.73      0.73        33

    accuracy                           0.69       198
   macro avg       0.69      0.67      0.68       198
weighted avg       0.69      0.69      0.68       198



In [ ]:
# Definition of the labels
labels_definition = config.id2label
print("Labels Definition:", labels_definition)

Labels Definition: {0: 'negative', 1: 'neutral', 2: 'positive'}


In [ ]:
# Assuming unlabeled_data is your DataFrame containing unlabeled text data

# Tokenize unlabeled text data
unlabeled_encodings = tokenizer(list(data['cleaned_tweet_vader']), truncation=True, padding=True, max_length=128, return_tensors='pt')

# Create TensorDataset for unlabeled data
unlabeled_dataset = TensorDataset(unlabeled_encodings['input_ids'], unlabeled_encodings['attention_mask'])

# Prepare DataLoader for unlabeled data
unlabeled_loader = DataLoader(unlabeled_dataset, batch_size=batch_size, sampler=SequentialSampler(unlabeled_dataset))

# Inference loop
model.eval()
all_preds = []
with torch.no_grad():
    for batch in tqdm(unlabeled_loader, desc='Inference', unit='batches'):
        input_ids, attention_mask = batch
        logits = model(input_ids, attention_mask=attention_mask).logits
        preds = torch.argmax(logits, dim=1)
        all_preds.extend(preds.cpu().numpy())

# Now all_preds contains the predicted labels for the unlabeled data


Inference:   0%|          | 20/8975 [03:54<29:50:33, 12.00s/batches]

In [ ]:
model = AutoModelForSequenceClassification.from_pretrained(MODEL)

# Define a class for data preparation
class SimpleDataset(torch.utils.data.Dataset):
    def __init__(self, tokenized_texts):
        self.tokenized_texts = tokenized_texts

    def __len__(self):
        return len(self.tokenized_texts["input_ids"])

    def __getitem__(self, idx):
        return {k: v[idx] for k, v in self.tokenized_texts.items()}

# Tokenize texts and create prediction dataset
def tokenize_texts(texts):
    tokenized_texts = tokenizer(texts, truncation=True, padding=True, max_length=128, return_tensors="pt")
    return SimpleDataset(tokenized_texts)

# Perform inference and transform predictions to labels
def predict_sentiment(texts):
    # Tokenize texts
    pred_dataset = tokenize_texts(texts)

    # Set up trainer for inference
    training_args = TrainingArguments(
        output_dir="./dummy_output_dir",  # Provide a dummy output directory
        per_device_eval_batch_size=8,   # Reduce batch size
        disable_tqdm=False,             # Enable tqdm progress bars
    )
    trainer = Trainer(
        model=model,
        args=training_args,
    )

    # Perform inference
    predictions = trainer.predict(pred_dataset)
    preds = predictions.predictions.argmax(-1)
    labels = pd.Series(preds).map(model.config.id2label)

    # Convert predictions to PyTorch tensor
    predictions_tensor = torch.tensor(predictions.predictions)

    # Calculate softmax scores
    scores = (torch.exp(predictions_tensor) / torch.exp(predictions_tensor).sum(-1, keepdim=True)).max(1)

    return labels, scores

# Example usage with 'cleaned_tweet' column
tweets = data['cleaned_tweet'].tolist()

# Calculate the total number of batches
batch_size = 64
total_batches = (len(tweets) + batch_size - 1) // batch_size

# Perform sentiment analysis in batches
labels, scores = [], []
for i in tqdm(range(total_batches)):
    start_idx = i * batch_size
    end_idx = min((i + 1) * batch_size, len(tweets))
    batch_tweets = tweets[start_idx:end_idx]
    batch_labels, batch_scores = predict_sentiment(batch_tweets)
    labels.extend(batch_labels)
    scores.extend(batch_scores)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/929 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/239 [00:00<?, ?B/s]

...

100%|█████████▉| 4748/4750 [24:56<00:00,  2.76it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|█████████▉| 4749/4750 [24:57<00:00,  2.98it/s]/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


100%|██████████| 4750/4750 [24:57<00:00,  3.17it/s]


Text: the curse on musk iis working :fire::umbrellawithraindrops::catface::catface::personjuggling::collision:
Predicted Label: negative


RuntimeError: a Tensor with 64 elements cannot be converted to Scalar

In [15]:
# Definition of the labels
labels_definition = config.id2label
print("Labels Definition:", labels_definition)

Labels Definition: {0: 'negative', 1: 'neutral', 2: 'positive'}


In [ ]:
data.to_csv("predicted_sentiments_data.csv", index=False)
# data['predicted_sentiment'] = data['predicted_sentiment'].map({'positive': 2, 'neutral': 1, 'negative': 0})